# Animating NEXRAD Level II Data
---

## Overview
   
Within this notebook, we will cover:

1. Exploring the "guts" of a NEXRAD radar file 
1. Animating a sequence of AWS-served NEXRAD Level 2 Radar scans
1. Multi-hour plots

## Prerequisites
| Concepts | Importance | Notes |
| --- | --- | --- |
| [Cartopy Intro](https://foundations.projectpythia.org/core/cartopy/cartopy.html) | Required | Projections and Features |
| [Matplotlib Basics](https://foundations.projectpythia.org/core/matplotlib/matplotlib-basics.html) | Required | Basic plotting |
| [Py-ART Basics](../foundations/pyart-basics) | Required | IO/Visualization |

- **Time to learn**: 20 minutes
---

## Imports

In [ ]:
import pyart
import fsspec
from metpy.plots import USCOUNTIES, ctables
import matplotlib.pyplot as plt
import cartopy.crs as ccrs
import cartopy.feature as cfeature
import warnings
from datetime import datetime as dt
from datetime import timedelta
import pandas as pd
import matplotlib
matplotlib.rcParams['animation.html'] = 'html5'
from matplotlib.animation import ArtistAnimation

warnings.filterwarnings("ignore")

## Select the time and NEXRAD site

In [ ]:
start_time = dt(2025,4,26,17)
start_time_str = dt.strftime(start_time, format="%Y%m%d%H")
site = 'KENX'

### Select number of hours. 1 hour is strongly recommended! 

In [ ]:
nHours = 4

Point to the [NOAA NEXRAD Level 2 S3 Bucket on AWS](https://noaa-nexrad-level2.s3.amazonaws.com/index.html)

In [ ]:
fs = fsspec.filesystem("s3", anon=True)

In [ ]:
fileList = []
for n in range(0, nHours):
    datTime = start_time + timedelta(hours = n)
    year = dt.strftime(datTime,format="%Y")
    month = dt.strftime(datTime,format="%m")
    day = dt.strftime(datTime,format="%d")
    hour = dt.strftime(datTime,format="%H")
    timeStr = f'{year}{month}{day}{hour}'

#   Depending on the year, the radar files will have different naming conventions. 
    pattern1 = f's3://noaa-nexrad-level2/{year}/{month}/{day}/{site}/{site}{year}{month}{day}_{hour}*V06'
    pattern2 = f's3://noaa-nexrad-level2/{year}/{month}/{day}/{site}/{site}{year}{month}{day}_{hour}*V*.gz'
    pattern3 = f's3://noaa-nexrad-level2/{year}/{month}/{day}/{site}/{site}{year}{month}{day}_{hour}*.gz'

    files = sorted(fs.glob(pattern1))

    if (len(files) == 0):
        files = sorted(fs.glob(pattern2))  

    if (len(files) == 0):
        files = sorted(fs.glob(pattern3))   

    fileList.extend(files)

If we have an empty list, either there are no files available for that site/date, or the file name does not match any of the patterns above. 

In [ ]:
if (len(fileList) == 0):
    print ("There are no files found for this date and location. Either try a different date/site, \
or browse the NEXRAD2 archive to see if the file name uses a different pattern.")
else:
    print (fileList)

## Read the Data into PyART

Read in the first radar file in the group and list the available fields.

In [ ]:
radar = pyart.io.read_nexrad_archive(f's3://{fileList[0]}')
list(radar.fields)

The `radar` object has a lot of useful data ... and *metadata*! One way to look at the attributes of any Python object is to use the `vars` function. It returns a Python `dictionary`; each dictionary `key` has an associated value ... which might be a single value ... a list of values ... another dictionary ... and so on.

In [ ]:
radarDict = vars(radar)

In [ ]:
radarDict

We can get a list of all the individual keys in the dictionary:

In [ ]:
radarDict.keys()

The first key is `time`. Let's look at it:

In [ ]:
radarDict['time']

It's also a Python dictionary! It's shorter than its parent's ... so we can see that there are six keys. Let's look at the first one, `units`.

In [ ]:
radarDict['time']['units']

It's a string ... and a useful one ... as it provides a base time that we can use to infer timestamps for the start of each of the individual sweeps that make up the full volume scan of this particular radar file.

Let's look at `time`'s `data` key:

In [ ]:
radar.time['data'] # equivalent to: radarDict['time']['data']

<div class="alert alert-info"><b>Note: </b>Each key in the top-level <code>radar</code> dictionary can be accessed as an <i>attribute</i> in the <code>radar</code> object itself. </div>

<div class="alert alert-warning"><b>Question: </b>What does each value represent, in terms of <i>time</i>?</div>

How many elements are in this array?

In [ ]:
len(radar.time['data'])

Other keys include `longitude` and `latitude`. Let's have a look at them:

In [ ]:
radar.longitude, radar.latitude

These are also dictionaries! What do you think the `data` keys represent in both of them?

Get the central longitude and latitude for the scan, which should correspond to the coordinates of the radar site. Older data may have these coordinates set to 0. If so, get the coordinates from a table, and update the `radar` object.

In [ ]:
def verify_radar_latlon (radar):
    if radar.longitude['data'] == 0 or radar.latitude['data'] == 0:
        print (f"No latitude/longitude for {site}; will get them from NEXRAD site table")
        nexrad_sites = pd.read_csv('/spare11/atm350/data/nexrad_sites.csv')
        site_row = nexrad_sites.query("siteID == @site")
        radar.longitude['data'], radar.latitude['data'] = site_row['X'].values, site_row['Y'].values
    return radar

In [ ]:
radar = verify_radar_latlon(radar)

Let's explore the `sweep_number`, `elevation` and `fixed_angle` keys.

In [ ]:
radarDict['sweep_number']

In [ ]:
radarDict['elevation']

In [ ]:
radarDict['elevation']['data']

What is the length of the data array associated with elevation?

In [ ]:
len(radarDict['elevation']['data'])

In [ ]:
radarDict['fixed_angle']['data']

Notice the first several fixed-elevation angles may be duplicated!

Let's look at the number of rays in each sweep.

In [ ]:
ssri = radarDict['sweep_start_ray_index']
ssri

In [ ]:
seri = radarDict['sweep_end_ray_index']
seri

In [ ]:
seri['data'] - ssri['data'] + 1

<div class="alert alert-info">The first eight sweeps, corresponding to the lowest 8 elevation angles, contain 720 rays. The next 12 contain 360.</div>

<div class="alert alert-warning"><b>Question:</b>What does this imply in terms of the resolution of the sweeps for these two groups?</div>

In [ ]:
cLon, cLat = radar.longitude['data'], radar.latitude['data']

Specify latitude and longitude bounds for the resulting maps, the resolution of the cartographic shapefiles, and the desired sweep level.

In [ ]:
lonW = cLon - 2
lonE = cLon + 2
latS = cLat - 2
latN = cLat + 2
domain = lonW, lonE, latS, latN

res = '10m'
sweep = 0

Define a function that will determine at which ray a particular sweep begins; also define some strings for the figure title.

In [ ]:
def nexRadSweepTimeElev (radar, sweep):
    
    sweepRayIndex = radar.sweep_start_ray_index['data'][sweep]

    baseTimeStr = radar.time['units'].split()[-1]
    baseTime = dt.strptime(baseTimeStr, "%Y-%m-%dT%H:%M:%SZ")

    timeSweep = baseTime + timedelta(seconds=radar.time['data'][sweepRayIndex])

    timeSweepStr = dt.strftime(timeSweep, format="%Y-%m-%d %H:%M:%S UTC")

    elevSweep = radar.fixed_angle['data'][sweep]
    elevSweepStr = f'{elevSweep:.1f}°'
    return timeSweepStr, elevSweepStr

In [ ]:
radar.sweep_start_ray_index

In [ ]:
radar.sweep_number

In [ ]:
field = 'reflectivity'
shortName = 'REFL'

## Create a single figure of reflectivity, zoomed into the area of interest.


<div class="alert alert-info"><b>PPI Display</b> We construct a pseudo Plan Position Indicator (PPI) display. A true PPI display has the radar antenna at its center, with distance from it and the height above ground drawn as concentric circles (Source: <a href=https://en.wikipedia.org/wiki/Plan_position_indicator">Wikipedia</a>)</div>

In [ ]:
# Creating color tables for reflectivity (every 5 dBZ starting with 5 dBZ):
ref_norm, ref_cmap = ctables.registry.get_with_steps('NWSReflectivity', 5, 5)

In [ ]:
ref_cmap

#### We'll add range rings to the display.

In [ ]:
# Call the function that creates the title string, among other things.
timeSweepStr, elevSweepStr = nexRadSweepTimeElev (radar, sweep)
titleStr = f'{site} {shortName} {elevSweepStr} {timeSweepStr}'

# Create our figure
fig = plt.figure(figsize=[15, 6])

# Set up a single axes and plot reflectivity
ax = plt.subplot(111, projection=ccrs.PlateCarree())
ax.set_extent ([lonW, lonE, latS, latN])

display = pyart.graph.RadarMapDisplay(radar)
ref_map = display.plot_ppi_map(field,sweep=sweep, vmin=20, vmax=80, ax=ax, raster=False, title=titleStr,
            colorbar_label='Equivalent Relectivity ($Z_{e}$) (dBZ)', norm=ref_norm, cmap=ref_cmap, resolution=res)
range_rings = display.plot_range_rings([10,50,100,200],ax=ax, col='brown',ls='dashed',lw=0.5)
# Add counties
ax.add_feature(USCOUNTIES, linewidth=0.5);

Next, let's create a function to create a plot, so we can loop over all the radar files of the specified hour.

In [ ]:
def plot_radar_refl (idx, site, radar):
    proj = ccrs.PlateCarree()
    # New axes with the specified projection
    ax = fig.add_subplot(111, projection=proj)
    ax.set_extent(domain)
    ax.add_feature(USCOUNTIES.with_scale('5m'),edgecolor='grey', linewidth=1, zorder = 3 )
    display = pyart.graph.RadarMapDisplay(radar)
    ref_map = display.plot_ppi_map(field,sweep=sweep, cmap=ref_cmap, norm=ref_norm, ax=ax, colorbar_flag = False, 
                title_flag = False, colorbar_label='Equivalent Relectivity ($Z_{e}$) (dBZ)', resolution=res)
    return ax 

<div class="alert alert-info"><b>Color bar omitted</b> Embedding the colorbar into an animation sequence is non-trivial ... so we do not include a colorbar here.</div>

Loop over the files. Save each image.

In [ ]:
backend_ =  matplotlib.get_backend() 
backend_

Set the Jupyter matplotlib backend to one that will not show the graphics inline (this will save time in notebook execution)

<div class="alert alert-warning"><b>Be patient!</b> For an hour's worth of radar files (which can be 15 or so if the radar is in precip mode) this cell, and the animation creation cell that follows, will take a few minutes!</div>

### Set an increment for how many individual frames we should skip. In general, this should be set to the same value as the number of hours, in order to keep the animation size as well as the time to create the animation manageable.

In [ ]:
incr = nHours

In [ ]:
matplotlib.use("Agg")  # Prevent showing stuff

meshes = []
fig = plt.figure(figsize=(10,10))
for n, name in enumerate(fileList[::nHours]):
    print (n, name, site)
    radar = pyart.io.read_nexrad_archive(f's3://{name}') 
    radar = verify_radar_latlon(radar)
    ax1 = plot_radar_refl(n, site, radar)
    timeSweepStr, elevSweepStr = nexRadSweepTimeElev (radar, sweep)
    titleStr = f'{site} {shortName} {elevSweepStr} {timeSweepStr}' 
    print (titleStr)
    title = ax1.text(0.5,0.92,titleStr,horizontalalignment='center',
     verticalalignment='center', transform=fig.transFigure, fontsize=15)
    meshes.append((ax1,title))

Set the Jupyter matplotlib backend to the default value, so we see output once again.

In [ ]:
matplotlib.use(backend_)

In [ ]:
anim = ArtistAnimation(fig, meshes)

Display the animation (this may take some time, depending on the number of frames)

In [ ]:
anim

Save the animation to the current directory (this may also take some time)

In [ ]:
anim.save(f'{site}_{start_time_str}_refl.mp4')

---
### Things to try
Create an animation for a time and site of interest. Download the mp4 file and try loading it in Powerpoint.


#### References
1. [NEXRAD data on AWS](https://registry.opendata.aws/noaa-nexrad/)
2. [Project Pythia Radar Cookbook](https://projectpythia.org/radar-cookbook)